In [1]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report

In [2]:
import pandas as pd

splits = {'train': 'split/train-00000-of-00001.parquet', 'validation': 'split/validation-00000-of-00001.parquet', 'test': 'split/test-00000-of-00001.parquet'}
df_train = pd.read_parquet("hf://datasets/dair-ai/emotion/" + splits["train"])
df_val = pd.read_parquet("hf://datasets/dair-ai/emotion/" + splits["validation"])
df_test = pd.read_parquet("hf://datasets/dair-ai/emotion/" + splits["test"])

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [3]:
x_train = df_train['text']
y_train = df_train['label']

In [4]:
x_val = df_val['text']
y_val = df_val['label']

In [5]:
x_test = df_test['text']
y_test = df_test['label']

In [6]:
df_train.head()

text  label
0                            i didnt feel humiliated      0
1  i can go from feeling so hopeless to so damned...      0
2   im grabbing a minute to post i feel greedy wrong      3
3  i am ever feeling nostalgic about the fireplac...      2
4                               i am feeling grouchy      3

In [7]:
df_val.head()

text  label
0  im feeling quite sad and sorry for myself but ...      0
1  i feel like i am still looking at a blank canv...      0
2                     i feel like a faithful servant      2
3                  i am just feeling cranky and blue      3
4  i can have for a treat or if i am feeling festive      1

In [8]:
df_test.head()

text  label
0  im feeling rather rotten so im not very ambiti...      0
1          im updating my blog because i feel shitty      0
2  i never make her separate from me because i do...      0
3  i left with my bouquet of red and yellow tulip...      1
4    i was feeling a little vain when i did this one      0

In [9]:
vectorizer = TfidfVectorizer()

In [10]:
x_train_tfidf = vectorizer.fit_transform(x_train)
x_val_tfidf =vectorizer.transform(x_val)
x_test_tfidf = vectorizer.transform(x_test)

In [11]:
model1 = LogisticRegression(max_iter=1000)

In [12]:
model1.fit(x_train_tfidf,y_train)

LogisticRegression(max_iter=1000)

In [13]:
model1_pred = model1.predict(x_test_tfidf)

In [14]:
model1_metrics = classification_report(y_test,model1_pred)
print(model1_metrics)

              precision    recall  f1-score   support

           0       0.89      0.93      0.91       581
           1       0.83      0.96      0.89       695
           2       0.82      0.58      0.68       159
           3       0.90      0.81      0.85       275
           4       0.87      0.78      0.82       224
           5       0.84      0.47      0.60        66

    accuracy                           0.86      2000
   macro avg       0.86      0.75      0.79      2000
weighted avg       0.86      0.86      0.86      2000



In [15]:
from sklearn.svm import SVC

In [16]:
model2 =SVC()
model2.fit(x_train_tfidf,y_train)

SVC()

In [17]:
model2_pred = model2.predict(x_test_tfidf)

In [18]:
model2_metrics = classification_report(y_test,model2_pred)
print(model2_metrics)

              precision    recall  f1-score   support

           0       0.89      0.92      0.90       581
           1       0.81      0.96      0.88       695
           2       0.88      0.53      0.66       159
           3       0.91      0.79      0.84       275
           4       0.87      0.79      0.83       224
           5       0.86      0.45      0.59        66

    accuracy                           0.85      2000
   macro avg       0.87      0.74      0.78      2000
weighted avg       0.86      0.85      0.85      2000



In [19]:
from transformers import AutoTokenizer, AutoModelForCausalLM
from huggingface_hub import login
import torch
device = torch.device("cuda")

login(token="")

tokenizer = AutoTokenizer.from_pretrained("Qwen/Qwen2.5-1.5B")
model = AutoModelForCausalLM.from_pretrained("Qwen/Qwen2.5-1.5B", device_map="auto")

def classify_batch_with_prompt(text_batch):
    prompts = [
        f"""You are a helpful assistant. Classify the following sentence into one of the following emotions: sadness, joy, love, anger, fear, surprise.

        Sentence: "{text}"
        Emotion:"""
        for text in text_batch
    ]

    inputs = tokenizer(
        prompts,
        return_tensors="pt",
        padding="longest",
        truncation=True,
        max_length=128
    ).to(device)

    outputs = model.generate(
        **inputs,
        max_new_tokens=10,
        eos_token_id=tokenizer.eos_token_id,
        pad_token_id=tokenizer.pad_token_id
    )

    results = []
    for i in range(outputs.shape[0]):
        generated_tokens = outputs[i, inputs.input_ids.shape[1]:]
        result_text = tokenizer.decode(generated_tokens, skip_special_tokens=True)
        emotion_part = result_text.strip()
        emotion = "unknown"
        if ":" in emotion_part:
            try: emotion = emotion_part.split(":")[-1].strip().split()[0].lower()
            except IndexError: pass
        elif emotion_part:
            try: emotion = emotion_part.split()[0].lower()
            except IndexError: pass

        valid_emotions = {"sadness", "joy", "love", "anger", "fear", "surprise"}
        if emotion not in valid_emotions and emotion != "unknown":

            emotion = "unknown"
        results.append(emotion)
    return results


label_map = {
    0: "sadness", 1: "joy", 2: "love",
    3: "anger", 4: "fear", 5: "surprise"
}

sample_y_labels = [label_map[label] for label in y_val]



batch_size = 32
qwen_preds_val = []

print(f"\nToplam {len(x_val)} örnek işlenecek. Batch size: {batch_size}")
for i in range(0, len(x_val), batch_size):
    batch_texts = x_val[i:i+batch_size]
    current_batch_num = i // batch_size + 1
    total_batches = (len(x_val) + batch_size - 1) // batch_size
    print(f"İşleniyor batch {current_batch_num}/{total_batches} ({len(batch_texts)} örnek)...")


    batch_predictions = classify_batch_with_prompt(batch_texts)
    qwen_preds_val.extend(batch_predictions)

print("\nİşlem tamamlandı.")


tokenizer_config.json:   0%|          | 0.00/7.23k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/2.78M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/1.67M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/7.03M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/684 [00:00<?, ?B/s]

...

İşleniyor batch 61/63 (32 örnek)...


A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


İşleniyor batch 62/63 (32 örnek)...


A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


İşleniyor batch 63/63 (16 örnek)...

İşlem tamamlandı.


In [20]:
valid_qwen_preds_val = [p for p in qwen_preds_val if p != "unknown"]
valid_sample_y_labels_val = [sample_y_labels[i] for i, p in enumerate(qwen_preds_val) if p != "unknown"]

if not valid_qwen_preds_val:
    print("Hiç geçerli tahmin üretilemedi.")
else:
    report_labels = list(label_map.values())
    print(classification_report(valid_sample_y_labels_val, valid_qwen_preds_val, labels=report_labels, zero_division=0))

              precision    recall  f1-score   support

     sadness       0.50      0.89      0.64        80
         joy       0.86      0.43      0.58        88
        love       0.20      0.42      0.27        24
       anger       0.41      0.25      0.31        28
        fear       0.90      0.27      0.42        33
    surprise       0.00      0.00      0.00        11

    accuracy                           0.51       264
   macro avg       0.48      0.38      0.37       264
weighted avg       0.61      0.51      0.50       264



Surprise label's f1 score is resulted with 0. I'll compare llm's prediction and true label

In [21]:
import pandas as pd

validation_set_dataframe = pd.DataFrame({
    'text': x_val,
    'true_label': sample_y_labels,
    'predicted_label': qwen_preds_val
})

incorrect_df = validation_set_dataframe[validation_set_dataframe['true_label'] != validation_set_dataframe['predicted_label']]

surprise_incorrect_df = incorrect_df[incorrect_df['true_label'] == 'surprise']

print("Hatalı tahminler(Validation Set):")
print(incorrect_df)

print("\n'Surprise' için hatalı tahminler:")
print(surprise_incorrect_df)

Hatalı tahminler(Validation Set):
                                                   text true_label  \
0     im feeling quite sad and sorry for myself but ...    sadness   
1     i feel like i am still looking at a blank canv...    sadness   
2                        i feel like a faithful servant       love   
3                     i am just feeling cranky and blue      anger   
4     i can have for a treat or if i am feeling festive        joy   
...                                                 ...        ...   
1995  im having ssa examination tomorrow in the morn...    sadness   
1996  i constantly worry about their fight against n...        joy   
1997  i feel its important to share this info for th...        joy   
1998  i truly feel that if you are passionate enough...        joy   
1999  i feel like i just wanna buy any cute make up ...        joy   

     predicted_label  
0            unknown  
1            unknown  
2            unknown  
3            unknown  
4         

In [22]:
confusion_counts = incorrect_df.groupby(['true_label', 'predicted_label']).size().unstack(fill_value=0)

print("\nHatalı Tahmin Karışıklık Sayıları:")
print(confusion_counts)


Hatalı Tahmin Karışıklık Sayıları:
predicted_label  anger  fear  joy  love  sadness  surprise  unknown
true_label                                                         
anger                0     1    2     4       14         0      247
fear                 1     0    0     5       18         0      179
joy                  4     0    0    22       24         0      616
love                 2     0    3     0        9         0      154
sadness              3     0    0     5        0         1      470
surprise             0     0    1     3        7         0       70


This indicates that the model has great difficulty or hesitations in choosing one of the 6 emotions specified for the given texts. Perhaps the prompt is not directive enough or the texts are ambiguous for the model.

->Looking at the surprise row, we see 0 predictions in the surprise column among the misclassified examples. Combined with the 0 00 F1 score from the classification report, this confirms that none of the validation examples with the true label "surprise" were correctly predicted as "surprise".
->Instead, 70 "surprise" examples were predicted as "unknown".
->The remaining "surprise" misclassifications were scattered among other labels: joy (1), love (3), and sadness (7).

Let's try to improve prompt. We gonna try few-shot prompting technique

In [23]:
def classify_with_prompt_FS(text):
    valid_labels = {"sadness", "joy", "love", "anger", "fear", "surprise"}

    prompt = f"""You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "{text}"
Emotion:"""

    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)
    outputs = model.generate(
        **inputs,
        max_new_tokens=3,
        do_sample=False,
        num_beams=1,
        pad_token_id=tokenizer.pad_token_id,
        eos_token_id=tokenizer.eos_token_id
    )

    result = tokenizer.decode(outputs[0], skip_special_tokens=True)
    print(f">> Raw model output: {result}")

    # "Emotion:" kısmından sonrasını al ve ilk kelimeyi çıkar
    raw_label = result.split("Emotion:")[-1].strip().split()[0].lower()

    return raw_label if raw_label in valid_labels else "unknown"


In [24]:

"""batch_size = 1

print(f"\nToplam {len(x_val)} örnek işlenecek. Batch size: {batch_size}")
for i in range(0, len(x_val), batch_size):
    batch_texts = x_val[i:i+batch_size]
    current_batch_num = i // batch_size + 1
    total_batches = (len(x_val) + batch_size - 1) // batch_size
    print(f"İşleniyor batch {current_batch_num}/{total_batches} ({len(batch_texts)} örnek)...")


    batch_predictions = classify_batch_with_prompt_FS(batch_texts)"""

from tqdm import tqdm
from sklearn.metrics import classification_report


qwen_preds_FS = []

print(f"\nToplam {len(x_val)} örnek işlenecek (batch size: 1)...")


for text in tqdm(x_val, desc="İşleniyor"):
    prediction = classify_with_prompt_FS(text)
    qwen_preds_FS.append(prediction)

# Sınıflandırma raporu
print("\nSınıflandırma Raporu:")
print(classification_report(sample_y_labels, qwen_preds_FS))



Toplam 2000 örnek işlenecek (batch size: 1)...


İşleniyor:   0%|          | 1/2000 [00:00<07:57,  4.18it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "im feeling quite sad and sorry for myself but ill snap out of it soon"
Emotion: sadness

Sentence


İşleniyor:   0%|          | 2/2000 [00:00<07:56,  4.19it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "i feel like i am still looking at a blank canvas blank pieces of paper"
Emotion: sadness

Sentence


...

İşleniyor: 100%|█████████▉| 1999/2000 [09:01<00:00,  3.59it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "i truly feel that if you are passionate enough about something and stay true to yourself you will succeed"
Emotion: love

Sentence


İşleniyor: 100%|██████████| 2000/2000 [09:01<00:00,  3.69it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "i feel like i just wanna buy any cute make up i see online or even the one"
Emotion: surprise

Sentence

Sınıflandırma Raporu:
              precision    recall  f1-score   support

       anger       0.68      0.39      0.49       275
        fear       0.71      0.31      0.43       212
         joy       0.83      0.30      


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [25]:
#filter the sample_y_labels list by indexes of non-'unknown' predictions in the qwen_preds_val_FS list
valid_qwen_preds_val_FS = [p for p in qwen_preds_FS if p != "unknown"]
# filter the sample_y_labels list by indexes of non-'unknown' predictions in the qwen_preds_val_FS list
valid_sample_y_labels_val = [sample_y_labels[i] for i, p in enumerate(qwen_preds_FS) if p != "unknown"]

if not valid_qwen_preds_val_FS:
    print("Hiç geçerli tahmin üretilemedi.")
else:
    report_labels = list(label_map.values()) # Sadece beklenen etiketler
    print(classification_report(valid_sample_y_labels_val, valid_qwen_preds_val_FS, labels=report_labels, zero_division=0))

              precision    recall  f1-score   support

     sadness       0.45      0.87      0.59       547
         joy       0.83      0.30      0.44       701
        love       0.24      0.36      0.29       176
       anger       0.68      0.39      0.50       270
        fear       0.71      0.31      0.43       210
    surprise       0.18      0.35      0.24        77

    accuracy                           0.48      1981
   macro avg       0.51      0.43      0.42      1981
weighted avg       0.61      0.48      0.47      1981



In [26]:
confusion_counts_1 = pd.crosstab(
    pd.Series(valid_sample_y_labels_val, name='True Label'),
    pd.Series(valid_qwen_preds_val_FS, name='Predicted Label')
)

print("\nHatalı Tahmin Karışıklık Sayıları (Valid Predictions Only):")
print(confusion_counts_1)


Hatalı Tahmin Karışıklık Sayıları (Valid Predictions Only):
Predicted Label  anger  fear  joy  love  sadness  surprise
True Label                                                
anger              106    11    5     5      127        16
fear                15    65    5    12      101        12
joy                  5     7  212   168      250        59
love                 6     3   11    64       73        19
sadness             22     4   15    16      476        14
surprise             2     2    8     6       32        27


Some salient points in your confusion matrix:

sadness → anger (127 errors)

sadness → joy (56 errors)

love → joy (168 errors) ⚠️

surprise → joy (59 errors)

This shows that

"joy" is over-preferred by the model (possibly acting as a default for positive or neutral emotion expressions).

"love" and "joy" are confused in terms of emotional positivity.

"sadness" is confused between "anger" and "joy". Maybe the context is not strong enough.

"surprise" is again confused with "joy".


# **PART 9**

In [27]:
from tqdm import tqdm
from sklearn.metrics import classification_report

qwen_preds_FS_Test = []

print(f"\nToplam {len(x_test)} örnek işlenecek (batch size: 1)...")

# tqdm
for text in tqdm(x_test, desc="İşleniyor"):
    prediction_1 = classify_with_prompt_FS(text)
    qwen_preds_FS_Test.append(prediction_1)




Toplam 2000 örnek işlenecek (batch size: 1)...


İşleniyor:   0%|          | 1/2000 [00:00<07:52,  4.23it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "im feeling rather rotten so im not very ambitious right now"
Emotion: sadness

Sentence


İşleniyor:   0%|          | 2/2000 [00:00<07:55,  4.20it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "im updating my blog because i feel shitty"
Emotion: sadness

Sentence


...

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "i feel that i am useful to my people and that gives me a great feeling of achievement"
Emotion: joy

Sentence


İşleniyor: 100%|█████████▉| 1999/2000 [09:04<00:00,  3.43it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "im feeling more comfortable with derby i feel as though i can start to step out my shell"
Emotion: joy

Sentence


İşleniyor: 100%|██████████| 2000/2000 [09:04<00:00,  3.67it/s]

>> Raw model output: You are a helpful assistant for classifying text into one of the following emotions:

sadness, joy, love, anger, fear, surprise.

You MUST respond with ONLY one of these words: sadness, joy, love, anger, fear, surprise.
No explanation. No other words.

Examples:

Sentence: "I feel so happy right now!"
Emotion: joy

Sentence: "This is the worst day of my life."
Emotion: sadness

Sentence: "I am so angry I could scream."
Emotion: anger

Sentence: "That sudden noise scared me half to death!"
Emotion: fear

Sentence: "I am deeply in love with this person."
Emotion: love

Sentence: "Wow, that was totally unexpected!"
Emotion: surprise

Sentence: "i feel all weird when i have to meet w people i text but like dont talk face to face w"
Emotion: sadness

Sentence


In [28]:
"""# Yeni tahmin listesi olan qwen_preds_val_FS'i kullanarak geçerli tahminleri ve karşılık gelen gerçek etiketleri filtrele
valid_qwen_preds_test_FS = [p for p in qwen_preds_FS if p != "unknown"]
# sample_y_labels listesini, qwen_preds_val_FS listesindeki 'unknown' olmayan tahminlerin index'lerine göre filtrele
valid_sample_y_labels_test = [sample_y_labels[i] for i, p in enumerate(qwen_preds_FS_Test) if p != "unknown"]

if not valid_qwen_preds_test_FS:
    print("Hiç geçerli tahmin üretilemedi.")
else:
    report_labels = list(label_map.values()) # Sadece beklenen etiketler
    print(classification_report(valid_sample_y_labels_test, valid_qwen_preds_test_FS, labels=report_labels, zero_division=0))"""

# Filter valid predictions and corresponding real tags using the new prediction list qwen_preds_FS_Test
# First let's find the indexes of non-‘unknown’ predictions
valid_indices_test = [i for i, p in enumerate(qwen_preds_FS_Test) if p != "unknown"]

# Let's filter both real tags and predictions using these indexes
valid_sample_y_labels_test = [sample_y_labels[i] for i in valid_indices_test]
valid_qwen_preds_test_FS = [qwen_preds_FS_Test[i] for i in valid_indices_test]


if not valid_qwen_preds_test_FS:
    print("Hiç geçerli tahmin üretilemedi.")
else:
    report_labels = list(label_map.values()) # Sadece beklenen etiketler
    print(classification_report(valid_sample_y_labels_test, valid_qwen_preds_test_FS, labels=report_labels, zero_division=0))

              precision    recall  f1-score   support

     sadness       0.30      0.58      0.40       542
         joy       0.41      0.15      0.22       699
        love       0.06      0.11      0.08       174
       anger       0.15      0.08      0.10       271
        fear       0.08      0.03      0.05       205
    surprise       0.04      0.07      0.05        81

    accuracy                           0.24      1972
   macro avg       0.17      0.17      0.15      1972
weighted avg       0.26      0.24      0.22      1972



In [29]:
confusion_counts_2 = pd.crosstab(
    pd.Series(valid_sample_y_labels_test, name='True Label'),
    pd.Series(valid_qwen_preds_test_FS, name='Predicted Label')
)

print("\nHatalı Tahmin Karışıklık Sayıları (Valid Predictions Only):")
print(confusion_counts_1)


Hatalı Tahmin Karışıklık Sayıları (Valid Predictions Only):
Predicted Label  anger  fear  joy  love  sadness  surprise
True Label                                                
anger              106    11    5     5      127        16
fear                15    65    5    12      101        12
joy                  5     7  212   168      250        59
love                 6     3   11    64       73        19
sadness             22     4   15    16      476        14
surprise             2     2    8     6       32        27


# Extra Credit - TinyBERT

In [30]:
from torch.utils.data import DataLoader
from datasets import Dataset

In [31]:
from transformers import AutoTokenizer, AutoModel
import torch
import numpy as np
from tqdm import tqdm

#for gpu
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Tokenizer and modl
tokenizer2 = AutoTokenizer.from_pretrained("google-bert/bert-base-uncased")
model_TB = AutoModel.from_pretrained("google-bert/bert-base-uncased").to(device)
model_TB.eval()


def get_embedding(text):
    inputs = tokenizer2(text, return_tensors="pt", truncation=True, padding="max_length", max_length=64).to(device)
    with torch.no_grad():
        outputs = model_TB(**inputs)
    return outputs.last_hidden_state[:, 0, :].squeeze().cpu().numpy()

X_train = np.array([get_embedding(text) for text in tqdm(df_train["text"])])
y_train = df_train["label"].values

X_val = np.array([get_embedding(text) for text in tqdm(df_val["text"])])
y_val = df_val["label"].values


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

100%|██████████| 2000/2000 [00:18<00:00, 105.83it/s]


In [35]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report

# Klasik model eğitimi
clf = LogisticRegression(max_iter=1000)
clf.fit(X_train, y_train)

# Tahmin ve metrikler
y_pred_val_emb = clf.predict(X_val)
print("🔹 [Embedding + LogisticRegression] Validation Set Sonuçları:")
print(classification_report(y_val, y_pred_val_emb, target_names=list(label_map.values())))


🔹 [Embedding + LogisticRegression] Validation Set Sonuçları:
              precision    recall  f1-score   support

     sadness       0.58      0.68      0.62       550
         joy       0.68      0.76      0.72       704
        love       0.51      0.26      0.35       178
       anger       0.52      0.39      0.44       275
        fear       0.50      0.48      0.49       212
    surprise       0.46      0.28      0.35        81

    accuracy                           0.60      2000
   macro avg       0.54      0.48      0.50      2000
weighted avg       0.58      0.60      0.58      2000



/usr/local/lib/python3.11/dist-packages/sklearn/linear_model/_logistic.py:465: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [32]:
train_data = Dataset.from_pandas(df_train)
val_data = Dataset.from_pandas(df_val)
test_data = Dataset.from_pandas(df_test)

In [33]:
def tokenize_function(examples):
    return tokenizer2(examples['text'], padding="max_length", truncation=True)

train_data = train_data.map(tokenize_function, batched=True)
val_data = val_data.map(tokenize_function, batched=True)
test_data = test_data.map(tokenize_function, batched=True)

train_loader = DataLoader(train_data, batch_size=16)
val_loader = DataLoader(val_data, batch_size=16)

Map:   0%|          | 0/16000 [00:00<?, ? examples/s]

Map:   0%|          | 0/2000 [00:00<?, ? examples/s]

Map:   0%|          | 0/2000 [00:00<?, ? examples/s]

In [34]:
import os
os.environ["WANDB_DISABLED"] = "true"

from transformers import BertForSequenceClassification, TrainingArguments, Trainer
#(etiket sayısı: 6)
model_cls = BertForSequenceClassification.from_pretrained("google-bert/bert-base-uncased", num_labels=6).to(device)

training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=3,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=64,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    report_to=None
)

trainer = Trainer(
    model=model_cls,
    args=training_args,
    train_dataset=train_data,
    eval_dataset=val_data,
)

trainer.train()

preds = trainer.predict(test_data)
y_pred = preds.predictions.argmax(axis=1)
y_true = test_data['label']

# Sonuçlar
from sklearn.metrics import classification_report
print(classification_report(y_true, y_pred, target_names=list(label_map.values())))

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at google-bert/bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Using the `WANDB_DISABLED` environment variable is deprecated and will be removed in v5. Use the --report_to flag to control the integrations used for logging result (for instance --report_to none).


              precision    recall  f1-score   support

     sadness       0.97      0.97      0.97       581
         joy       0.94      0.96      0.95       695
        love       0.89      0.78      0.83       159
       anger       0.92      0.93      0.92       275
        fear       0.88      0.92      0.90       224
    surprise       0.76      0.76      0.76        66

    accuracy                           0.93      2000
   macro avg       0.89      0.89      0.89      2000
weighted avg       0.93      0.93      0.93      2000

